In [6]:
import plotly.express as px
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
from scipy.special import binom
import dash
from dash import dcc
from dash import html
from dash.dependencies import Input, Output
import plotly.graph_objs as go
import plotly.offline as pyo

Drop Rates

In [24]:
'''
Drop rates acquired from crowd sourced osrs.wiki data  as of August 08, 2023
'''
rates={
    'vardorvis' : 1/480,
    'duke' : 1/288,
    'leviathan' : 1/320,
    'whisperer' : 1/205
}

r = 3

In [9]:
def nbinomial_pmf(r, p, y):
    '''
    Negative binomial probability function. r = 1 is the special case of the geometric probability function.
    Values of r larger than 3 may create numbers too large to be represented correctly using float64. 
    ---Parameters---
    r (int) number of successes 
    p (float) probability of a success of a bernoulli trial 
    y (int) y'th iid bernoulli trial
    ---Returns---
    Probability of getting the r'th success on exactly the y'th trial
    '''
    q = 1 - p
    if y < r:
        return 0
    else:
        return binom(y - 1, r - 1) * (p**r) * (q**(y-r))

In [10]:
def nbinomial_pmf_dict(r, p, n):
    '''
    Creates dictionary of negative binomial probability mass function values.
    ---Parameters---
    r (int) number of successes 
    p (float) probability of a success of a bernoulli trial 
    n (int) number of iid bernoulli trials to calculate
    ---Returns---
    Dictionary of pmf values
    '''
    pmf_dict = {}
    for y in range(1,n+1):
        pmf_dict[y]=nbinomial_pmf(r, p, y)
    return pmf_dict

In [11]:
def nbinomial_cdf_dict(pmf_dict):
    '''
    Creates dictionary of negative binomial cumulative distribution function values.
    ---Parameters---
    pmf_dict (dict) dictionary of pmf values to cumulate to create cdf
    ---Returns---
    Dictionary of cdf values
    '''
    cdf_dict={}
    cum_sum=0
    for y in pmf_dict.keys():
        cdf_dict[y]=cum_sum + pmf_dict[y]
        cum_sum = cdf_dict[y]
    return cdf_dict

In [42]:
def create_df(n, r):
    '''
    Compiles drop rate cdf data from each of the bosses and contructs a DataFrame
    ---Parameters---
    n (int) number of kill count to calculate and show
    r (int) number of successes
    ---Returns---
    Pandas DataFrame of cdf drop data
    '''
    data_list={}
    data_list['kill count'] = list(range(1,n+1))
    for boss, drop_rate in rates.items():
        data_list[boss + '_current'] = nbinomial_cdf_dict(nbinomial_pmf_dict(r, drop_rate,n)).values()
        data_list[boss + '_regular'] = nbinomial_cdf_dict(nbinomial_pmf_dict(1, drop_rate * (1/r), n)).values()
    return pd.DataFrame(data=data_list)

In [43]:
f=create_df(8000, 3)
f.head()

kill count  vardorvis_current  vardorvis_regular  duke_current  \
0           1       0.000000e+00           0.000694  0.000000e+00   
1           2       0.000000e+00           0.001388  0.000000e+00   
2           3       9.042245e-09           0.002082  4.186225e-08   
3           4       3.611247e-08           0.002775  1.670129e-07   
4           5       9.014012e-08           0.003467  4.164452e-07   

   duke_regular  leviathan_current  leviathan_regular  whisperer_current  \
0      0.001157       0.000000e+00           0.001042       0.000000e+00   
1      0.002313       0.000000e+00           0.002082       0.000000e+00   
2      0.003468       3.051758e-08           0.003122       1.160749e-07   
3      0.004622       1.217842e-07           0.004160       4.626010e-07   
4      0.005774       3.037471e-07           0.005197       1.152273e-06   

   whisperer_regular  
0           0.001626  
1           0.003249  
2           0.004870  
3           0.006488  
4           0.008104

In [71]:
f['rate']=f['kill count']/1440
f['current']=f['vardorvis_current']
f['regular']=f['vardorvis_regular']
f['difference']=f['current']-f['regular']

In [72]:
f.head()

kill count  vardorvis_current  vardorvis_regular  duke_current  \
0           1       0.000000e+00           0.000694  0.000000e+00   
1           2       0.000000e+00           0.001388  0.000000e+00   
2           3       9.042245e-09           0.002082  4.186225e-08   
3           4       3.611247e-08           0.002775  1.670129e-07   
4           5       9.014012e-08           0.003467  4.164452e-07   

   duke_regular  leviathan_current  leviathan_regular  whisperer_current  \
0      0.001157       0.000000e+00           0.001042       0.000000e+00   
1      0.002313       0.000000e+00           0.002082       0.000000e+00   
2      0.003468       3.051758e-08           0.003122       1.160749e-07   
3      0.004622       1.217842e-07           0.004160       4.626010e-07   
4      0.005774       3.037471e-07           0.005197       1.152273e-06   

   whisperer_regular      rate       current   regular  difference  
0           0.001626  0.000694  0.000000e+00  0.000694   -0.000694  
1           0.003249  0.001389  0.000000e+00  0.001388   -0.001388  
2           0.004870  0.002083  9.042245e-09  0.002082   -0.002082  
3           0.006488  0.002778  3.611247e-08  0.002775   -0.002775  
4           0.008104  0.003472  9.014012e-08  0.003467   -0.003467

In [76]:
f[f['kill count']==360]

kill count  vardorvis_current  vardorvis_regular  duke_current  \
359         360           0.040332           0.221267       0.13124   

     duke_regular  leviathan_current  leviathan_regular  whisperer_current  \
359      0.340918           0.104388           0.312845           0.257494   

     whisperer_regular  rate   current   regular  difference  
359           0.443363  0.25  0.040332  0.221267   -0.180935

In [75]:
fig = px.line(f, x='rate', 
              y=['current', 'regular', 'difference'], 
              labels={'value': 'Probability', 'variable':'Legend'},
              title='Cumulative Distribution Function for Vestiges Using Current and Regular Drop Mechanics'
             )
fig.update_layout(hovermode='x',
                 yaxis=dict(tickmode='linear', 
                           tick0=0,
                           dtick=.1))
fig.show()

In [46]:
fig = px.line(f, x='kill count', 
              y=['vardorvis_current', 'vardorvis_regular',
                 'duke_current', 'duke_regular',
                 'leviathan_current','leviathan_regular',
                 'whisperer_current', 'whisperer_regular',], 
              labels={'kill count': 'Kill Count', 'value': 'Probability'},
              title='Cumulative Distribution Functions for Vestiges using current and regular drop mechanics'
             )
fig.update_layout(hovermode='x')
fig.show()

In [22]:
output_file = 'dt2.html'
pyo.plot(fig, filename=output_file, auto_open=False)

print(f"The graph has been saved as '{output_file}'.")

The graph has been saved as 'dt2.html'.
